**Introduction**

Pulsars are neutron stars originated from the collapsed core of a giant star (10 to 29 solar masses).<br>
Pulsars have strong magnetic fields and they keep emitting two beams of electromagnetic radiation in opposite directions while rapidly rotating. As they keep rotating their beams traverse the sky, and when these beams point to the Earth, we can detect them. The reason why they're called pulsars is that from Earth we keep seeing such light beams going in and out of view, thus producing a flickering or 'pulsing' effect, similarly to a lighthouse. Thus for us pulsars produce a periodic pattern, and pulsar detection is based on the observation of such repeated patterns of radio emissions with radio telescopes.<br><br><p align="center">
  <img width="460" height="300" src="https://media0.giphy.com/media/l3dj5M4YLaFww31V6/giphy.gif">
  <center>Pulsar spinning</center>
</p>

The problem is that noise and radio frequency interference (RFI) can produce pulsar-like signals, making it difficult to distinguish among real pulsars and false positives. <br>
In this work, we use several Machine Learning models to identify true pulsar stars while minimizing the false positive rate. We assess the models's performances and see which is the best model for detecting real pulsars.

**Libraries**

First of all we import the libraries needed for our work.

In [0]:
#@title
import os
from os import path

import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from sklearn.model_selection import train_test_split, GridSearchCV, learning_curve, StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import confusion_matrix, roc_curve, auc, accuracy_score, precision_score, recall_score, f1_score
from sklearn.svm import SVC
from scipy.stats import norm
import warnings

**Dataset: HTRU2**

The HTRU2 dataset describes a pulsar candidates sample collected during an HTRU (High Time Resolution Universe) survey. It is available at the following address: http://archive.ics.uci.edu/ml/datasets/HTRU2 <br>
Pulsar candidates are detected signals who could potentially come from pulsar stars. <br>
For each candidate we have 8 features which derive from the integrated pulse profile (IP) and from the dispersion measure signal-to-noise ratio (DM-SNR) curve, which are two physics properties related to radio emissions. <br>
The individual pulses of a pulsar don't have a constant shape, thus they cannot be used to uniquely identify each pulsar. 
But astronomers found out that by stacking up the individual pulses over a certain period, the resultant average 'integrated' pulse profile would be now able to identify a specific pulsar. So the integrated pulse profile is the pulsar's fingerprint: each pulsar is characterized by a unique pulse profile shape, by which we can distinguish among different pulsars.

<p align="center">
  <img width="460" height="500" src="https://cdn.iopscience.com/images/0004-637X/524/2/1008/Full/fg1.gif">
  <center>Single pulses (in the center) and integrated average profile (on the bottom).</center>
<br>

Furthermore, the electromagnetic pulse emitted by the pulsar is composed by different frequencies. By interacting with the interstellar medium (ISM) in the space, lower frequencies are slowed down and so they arrive to us with some delay. This effect is known as 'dispersion': higher frequencies travel quicker and slower ones travel more slowly.

<p align="center">
  <img width="460" height="500" src="https://casper.ssl.berkeley.edu/astrobaki/images/thumb/f/f5/Pulsar_dm.png/600px-Pulsar_dm.png">
  <center>Dispersion: how frequency affects the arrival times (on the top). <br>
   De-dispersion: wait for the lower frequencies to reconstruct the integrated pulse profile, by summing up over all the frequency channels (on the bottom).
</center>
<br>

SNR is a quantity measuring the level of a signal with respect to the level of background noise. DM is a quantity representing to which degree a signal gets dispersed,  varying depending on the distance from the signal source and the quantity of ionized plasma present in the interstellar medium that the signal has to traverse.
As we cannot know the DM a priori, to measure how much the signal gets dispersed the astronomers have to to try and test different DM values in a wide range. <br>
The DM-SNR curve describes the signal-to-noise ratio as a function of a range of trial dispersion measures, and it serves as a tool for astronomers for better identifying pulsars.
For larger SNR values it is less likely that the signal comes from simple white noise, hence the DM-SNR curve of a pulsar would peak at a nonzero value unless affected severely by interference.

<br>
<p align="center">
  <img width="460" height="300" src="https://github.com/frandi93/Images/blob/master/DM_curve.png?raw=true" >
  <center>DM-SNR curve example with peak value at DM = 195.7</center>
<br>


**Features**

We have 8 features in total: 4 are statistics derived from integrated profile, and the other 4 are statistics derived from the DM-SNR curve.
<br><br>

<p align="center">
  <img width="460" height="300" src="https://github.com/frandi93/Images/blob/master/pulsar_features.png?raw=true" >
</p>

*Statistics of the integrated profile*
<br><br>
The first feature is the first statistical moment (mean) of the integrated pulse profile, calculated over the sampled profile: 
<br><br>
\begin{equation*}
Prof_\mu  = \frac{1}{n}\sum_{i=1}^n p_i
\end{equation*}
<br>
The second feature is the second statistical moment (variance). Variance is a measure of the spread, indicating how far the samples are away from the mean in a data distribution:<br>
\begin{equation*}
Prof_\sigma  = \sqrt{\frac{\sum\limits_{i=1}^N (p_i -Prof_\mu)^2}{n-1}}
\end{equation*}
<br>
The third feature (excess kurtosis) derives from the fourth statistical moment (kurtosis). Kurtosis is a measure of the number of samples in the distribution tails (outliers). Heavy-tailed distributions have high kurtosis, while distributions with light tails have low kurtosis. Excess kurtosis measures the difference between the kurtosis of a generic distribution and the kurtosis of a normal distribution. As for a normal distribution the kurtosis *k* is always equal to 3, the excess kurtosis of a distribution is defined as *k*-3:
<br><br>
\begin{equation*}
Prof_k  = \frac{\frac{1}{n}\sum\limits_{i=1}^N(p_i -Prof_\mu)^4}{(\frac{1}{n}\sum\limits_{i=1}^N(p_i -Prof_\mu)^2)^2}-3
\end{equation*}
<br>
The fourth feature is the third statistical moment (skewness). Skewness is used together with kurtosis to analyze the likelihood of events falling in the tails of a distribution. Skewness measures the unbalance of a distribution, which is how much the curve is skewed to the left or to the right with respect to the mean:
<br>
\begin{equation*}
Prof_s  = \frac{\frac{1}{n}\sum\limits_{i=1}^N(p_i -Prof_\mu)^3}{\sqrt{\frac{1}{n-1}\sum\limits_{i=1}^N(p_i -Prof_\mu)^2}^3}
\end{equation*}


*Statistics of the DM-SNR curve*
<br><br>
The same 4 statistics are derived from the DM-SNR curve:
<br>
\begin{equation*}
DM_\mu  = \frac{1}{n}\sum_{i=1}^n d_i
\end{equation*}
<br>

\begin{equation*}
DM_\sigma  = \sqrt{\frac{\sum\limits_{i=1}^N (d_i -DM_\mu)^2}{n-1}}
\end{equation*}
<br>

\begin{equation*}
DM_k  = \frac{\frac{1}{n}\sum\limits_{i=1}^N(d_i -DM_\mu)^4}{(\frac{1}{n}\sum\limits_{i=1}^N(d_i -DM_\mu)^2)^2}-3
\end{equation*}
<br>

\begin{equation*}
DM_s  = \frac{\frac{1}{n}\sum\limits_{i=1}^N(d_i -DM_\mu)^3}{\sqrt{\frac{1}{n-1}\sum\limits_{i=1}^N(d_i -DM_\mu)^2}^3}
\end{equation*}


In [3]:
#@title
if not path.exists("HTRU2.zip"):
  print('Downloading HTRU2 dataset...')
  !wget https://archive.ics.uci.edu/ml/machine-learning-databases/00372/HTRU2.zip
  !unzip HTRU2.zip
  print('HTRU2 dataset downloaded and extracted correctly!')

--2020-04-19 20:13:50--  https://archive.ics.uci.edu/ml/machine-learning-databases/00372/HTRU2.zip
Resolving archive.ics.uci.edu (archive.ics.uci.edu)... 128.195.10.252
Connecting to archive.ics.uci.edu (archive.ics.uci.edu)|128.195.10.252|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1563015 (1.5M) [application/x-httpd-php]
Saving to: ‘HTRU2.zip’

HTRU2.zip           100%[===================>]   1.49M  1.78MB/s    in 0.8s    

2020-04-19 20:13:51 (1.78 MB/s) - ‘HTRU2.zip’ saved [1563015/1563015]

Archive:  HTRU2.zip
  inflating: HTRU_2.csv              
  inflating: HTRU_2.arff             
  inflating: Readme.txt              
HTRU2 dataset downloaded and extracted correctly!


**Data Exploration**

In [4]:
#@title
pulsar_df = pd.read_csv("HTRU_2.csv")
pulsar_df.columns = ['Mean of the integrated profile','Standard deviation of the integrated profile','Excess kurtosis of the integrated profile','Skewness of the integrated profile',
                     'Mean of the DM-SNR curve','Standard deviation of the DM-SNR curve','Excess kurtosis of the DM-SNR curve','Skewness of the DM-SNR curve','Target Class']
pulsar_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17897 entries, 0 to 17896
Data columns (total 9 columns):
 #   Column                                        Non-Null Count  Dtype  
---  ------                                        --------------  -----  
 0   Mean of the integrated profile                17897 non-null  float64
 1   Standard deviation of the integrated profile  17897 non-null  float64
 2   Excess kurtosis of the integrated profile     17897 non-null  float64
 3   Skewness of the integrated profile            17897 non-null  float64
 4   Mean of the DM-SNR curve                      17897 non-null  float64
 5   Standard deviation of the DM-SNR curve        17897 non-null  float64
 6   Excess kurtosis of the DM-SNR curve           17897 non-null  float64
 7   Skewness of the DM-SNR curve                  17897 non-null  float64
 8   Target Class                                  17897 non-null  int64  
dtypes: float64(8), int64(1)
memory usage: 1.2 MB


In [5]:
pulsar_df.head()

Mean of the integrated profile  ...  Target Class
0                      102.507812  ...             0
1                      103.015625  ...             0
2                      136.750000  ...             0
3                       88.726562  ...             0
4                       93.570312  ...             0

[5 rows x 9 columns]

In [6]:
pulsar_df.describe()

Mean of the integrated profile  ...  Target Class
count                    17897.000000  ...   17897.00000
mean                       111.078321  ...       0.09158
std                         25.652705  ...       0.28844
min                          5.812500  ...       0.00000
25%                        100.929688  ...       0.00000
50%                        115.078125  ...       0.00000
75%                        127.085938  ...       0.00000
max                        192.617188  ...       1.00000

[8 rows x 9 columns]

**Feature Correlation Visualization**

In [7]:
#@title
pulsar_df = pulsar_df.rename(columns={'Mean of the integrated profile':"MEAN_IS",
                                      'Standard deviation of the integrated profile':"STD_IS",
                                      'Excess kurtosis of the integrated profile':"KURT_IS",
                                      'Skewness of the integrated profile':"SKEW_IS", 
                                      'Mean of the DM-SNR curve':"MEAN_DM",
                                      'Standard deviation of the DM-SNR curve':"STD_DM",
                                      'Excess kurtosis of the DM-SNR curve':"KURT_DM",
                                      'Skewness of the DM-SNR curve':"SKEW_DM",
                                      'Target Class':"TARGET"
                                      })

corr_mat = pulsar_df.corr()
x = corr_mat.columns.to_list()
y = corr_mat.columns.to_list()
z = corr_mat.values.tolist()

annotations=[]
for n, row in enumerate(z):
  for m, val in enumerate(row):
    annotations.append(dict(text=("{:.2f}".format(z[n][m])), x=x[m], y=y[n], xref='x1', yref='y1', showarrow=False))
                              
data = [dict(type='heatmap', z=pulsar_df.corr().values, x=corr_mat.columns, y=corr_mat.columns, colorscale = 'Blues')]

layout = dict(xaxis=dict(title='Feature correlation matrix'), autosize=False, width=800, height=800, annotations=annotations)

fig = go.Figure(data=data, layout=layout)  
fig.show()

**Target Distribution Visualization**

In [8]:
#@title
y = pulsar_df["TARGET"].value_counts()
target_classes = ["Non-Pulsar", "Pulsar"]

data = [dict(type='bar', x=target_classes, y=y.values, text=y, textposition='auto', marker = dict(color = ['blue','red']))]
                                                                      
layout = go.Layout(title='Target Distribution', autosize=False, width=600, height=600, yaxis=dict(title='Samples'))
fig = go.Figure(data=data, layout=layout)
fig.show()

**Pairwise Feature relationship Visualization**

In [9]:
#@title
textd = ['Non-Pulsar' if cl==0 else 'Pulsar' for cl in pulsar_df['TARGET']]
labels = pulsar_df.drop('TARGET', axis=1).columns
dimensions = []
for i in range(len(labels)):
  dimensions.append(dict(label=labels[i], values=pulsar_df[labels[i]]))

fig = go.Figure(data=go.Splom(dimensions=dimensions, diagonal_visible=False, marker=dict(color=pulsar_df['TARGET'], size=5, colorscale='Bluered', line=dict(width=0.5,color='rgb(230,230,230)')), text=textd))

fig.update_layout(title='Pair Plot', dragmode='select', width=1300, height=1300, hovermode='closest')
fig.show()

**Mean and Standard Deviation Boxplots**

In [10]:
#@title
not_pulsar = pulsar_df[pulsar_df["TARGET"] == 0]
pulsar = pulsar_df[pulsar_df["TARGET"] == 1]

fig = go.Figure()

for col in pulsar_df.drop('TARGET', axis=1).columns:
  fig.add_trace(go.Violin(y=not_pulsar[col], box_visible=True, meanline_visible=True, x0='Non-Pulsar', name='Non-Pulsar', visible=False))
for col in pulsar_df.drop('TARGET', axis=1).columns:
  fig.add_trace(go.Violin(y=pulsar[col], box_visible=True, meanline_visible=True, x0='Pulsar', name='Pulsar', visible=False))

fig.data[0].visible = True
fig.data[8].visible = True

steps = []
for i in range(8):
  step = dict(method="restyle", args=["visible", [False] * len(fig.data)], label = pulsar_df.columns[i])
  step["args"][1][i] = True
  step["args"][1][i+8] = True
  steps.append(step)

sliders = [dict(active=8, currentvalue = dict(prefix = "Feature: "), pad={"t": 50}, steps=steps)]

fig.update_layout(sliders=sliders)

fig.show()

**Data Preprocessing**

In [11]:
#@title
X = pulsar_df.drop('TARGET', axis=1)
y = pulsar_df['TARGET']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=1, stratify=y)

scaler = StandardScaler().fit(X_train)
X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

y_train = y_train.reset_index(drop=True)
y_test = y_test.reset_index(drop=True)

labels = ["Non-Pulsar", "Pulsar"]
fig = make_subplots(rows=1, cols=2, specs=[[{'type':'domain'}, {'type':'domain'}]])
fig.add_trace(go.Pie(labels=labels, values=y_train.value_counts(), name="Train Set", textinfo='label+percent', pull=[0, 0.1]), 1, 1)
fig.add_trace(go.Pie(labels=labels, values=y_test.value_counts(), name="Test Set", textinfo='label+percent', pull=[0, 0.1]), 1, 2)

fig.update_layout(title_text="Train and Test sets class proportions", 
                  annotations=[dict(text='Train', x=0.05, y=0.5, font_size=20, showarrow=False), dict(text='Test', x=0.62, y=0.5, font_size=20, showarrow=False)])
fig.show()

**PCA**

In [12]:
#@title
pca = PCA(random_state=1)
X_train_pca = pca.fit_transform(X_train)

exp_var = pca.explained_variance_
tot_exp_var = sum(exp_var)
comp_exp_var = [(i / tot_exp_var) * 100 for i in sorted(exp_var, reverse=True)]
cum_exp_var = np.cumsum(comp_exp_var)

comp_exp_var_trace = dict(type='bar', x=['PC%s' %i for i in range(1,9)], y=comp_exp_var, name='Individual')

cum_exp_var_trace = dict(type='scatter', x=['PC%s' %i for i in range(1,9)],  y=cum_exp_var, name='Cumulative', line_shape='hvh')

data = [comp_exp_var_trace, cum_exp_var_trace]

annotation_list = list([dict(x=1.16, y=1.05, xref='paper', yref='paper', showarrow=False)])
layout = dict(title='Variance explained by the principal components', yaxis=dict(title='Explained variance %'), annotations=annotation_list)

fig = go.Figure(data=data, layout=layout)
fig.show()

pca_5D = PCA(n_components=5, random_state=1).fit_transform(X_train)

**PCA Visualization**

In [13]:
#@title
def pulsar_split(sample_set, label_set):
  not_pulsar = []
  pulsar = []
  for i in range(len(label_set)):
    if label_set[i] == 0:
      not_pulsar.append(sample_set[i])
    elif label_set[i] == 1:
      pulsar.append(sample_set[i])
  return np.array(not_pulsar), np.array(pulsar)


pca = PCA(n_components=2, random_state=1)
pca_2D = pca.fit_transform(X_train)
not_pulsar, pulsar = pulsar_split(pca_2D, y_train)

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "scene"}]], subplot_titles=("PCA 2D", "PCA 3D"))
      
fig.add_trace(go.Scatter(x=not_pulsar[:,0], y=not_pulsar[:,1], mode='markers', name='Non-Pulsar', marker=dict(color='blue', size=11, opacity=0.7)), row=1, col=1)
fig.add_trace(go.Scatter(x=pulsar[:,0], y=pulsar[:,1], mode='markers', name='Pulsar', marker=dict(color='red', size=11, opacity=0.7)), row=1, col=1)

pca = PCA(n_components=3, random_state=1)
pca_3D = pca.fit_transform(X_train)
not_pulsar, pulsar = pulsar_split(pca_3D, y_train)

fig.add_trace(go.Scatter3d(x=not_pulsar[:,0], y=not_pulsar[:,1], z=not_pulsar[:,2], mode='markers', name='Non-Pulsar', marker=dict(color='blue', size=11, opacity=0.7)), row=1, col=2)
fig.add_trace(go.Scatter3d(x=pulsar[:,0], y=pulsar[:,1], z=pulsar[:,2], mode='markers', name='Pulsar', marker=dict(color='red', size=11, opacity=0.7)), row=1, col=2)

fig.update_xaxes(title_text="PC1", row=1, col=1)
fig.update_yaxes(title_text="PC2", row=1, col=1)

fig.update_layout(scene = dict(xaxis = dict(title='PC1'), yaxis = dict(title='PC2'), zaxis = dict(title='PC3')))
fig.show()

**LDA for Dimesionality Reduction**

In [14]:
#@title
lda = LinearDiscriminantAnalysis(n_components=1)
lda_1D = lda.fit(X_train, y_train).transform(X_train)

not_pulsar, pulsar = pulsar_split(lda_1D, y_train)

mean_not_pulsar, std_not_pulsar = norm.fit(not_pulsar)
mean_pulsar, std_pulsar = norm.fit(pulsar)
mean, std = norm.fit(lda_1D)

X = np.linspace(-6, 13, 10000)
pdf = norm.pdf(X, mean, std)
pdf_not_pulsar = norm.pdf(X, mean_not_pulsar, std_not_pulsar)
pdf_pulsar = norm.pdf(X, mean_pulsar, std_pulsar)

data = []

pulsar = np.concatenate([np.array(i) for i in pulsar])
data.append(dict(type='scatter', x=pulsar, y=np.zeros(len(pulsar)), mode='markers', name='Pulsar', marker=dict(color='Red', size=6, opacity=0.7)))
not_pulsar = np.concatenate([np.array(i) for i in not_pulsar])
data.append(dict(type='scatter', x=not_pulsar, y=np.zeros(len(not_pulsar)), mode='markers', name='Non-Pulsar', marker=dict(color='blue', size=6, opacity=0.7)))
data.append(dict(type='scatter', x=np.asarray(mean_pulsar), y=[0], mode='markers', name='Pulsar PDF mean', marker=dict(color='red', symbol='x', size=30, opacity=0.7)))
data.append(dict(type='scatter', x=np.asarray(mean_not_pulsar), y=[0], mode='markers', name='Non-Pulsar PDF mean', marker=dict(color='blue', symbol='x', size=30, opacity=0.7)))
data.append(dict(type='scatter', x=np.asarray(mean), y=[0], mode='markers', name='All stars PDF mean', marker=dict(color='black', symbol='x', size=30, opacity=0.7)))
data.append(dict(type='scatter', x=X, y=pdf_pulsar, mode='lines', name='Pulsar PDF', marker=dict(color='red', size=3, opacity=0.7)))
data.append(dict(type='scatter', x=X, y=pdf_not_pulsar, mode='lines', name='Non-Pulsar PDF', marker=dict(color='blue', size=3, opacity=0.7)))
data.append(dict(type='scatter', x=X, y=pdf, mode='lines', name='All stars PDF', marker=dict(color='black', size=3, opacity=0.7)))

layout = dict(xaxis=dict(title='Discriminating Hyperplane'), yaxis=dict(title='PDFs'))
fig = go.Figure(data=data, layout=layout)
fig.show()

**Plotting functions and Initialization**

After the dataset exploration and description, let's now start with the classification phase.<br>
The choosen algorithm for this analisys are:
* LDA
* Logistic Regression
* Decision Tree
* K-NN
* Random Forest
* Linear SVM
* Gaussian SVM

The different version of the dataset are:
* the training set
* PCA reduced training set
* LDA reduced training set

A grid search with 5-Fold cross validation is performed for each different version of the dataset and for each algorithm.<br>
For a visual impression of the performances the choosen plot are:
* confusion matrix 
* learning curve graph
* ROC curve
* feature importance graph (only for Random Forest)

A comparision will be done after all the single applications.


In [0]:
#@title
def grid_search_matrix(estimator, X_train, y_train, X_test, y_test, cv, title, parameters, fig_matrix, fig_roc, col, col_roc=2, var_importance=False, n_jobs=None):
  if cv:
    grid_search = GridSearchCV(estimator, parameters, cv = cv, scoring='f1', return_train_score=True, n_jobs=n_jobs).fit(X_train, y_train)
    #print(grid_search.best_estimator_)
    if var_importance:
      plot_var_importance(grid_search.best_estimator_, pulsar_df)
    plot_confusion_matrix(grid_search, X_train, fig_matrix, col, "Confusion Matrices")
    plot_learning_curve(grid_search, X_train, y_train, cv)
    plot_roc_curve(grid_search.best_estimator_, title, X_test, y_test, fig_roc)

    return grid_search.best_estimator_  
  else:
    estimator.fit(X_train, y_train)
    plot_confusion_matrix(estimator, X_train, fig_matrix, col)
    plot_learning_curve(estimator, X_train, y_train, cv)
    plot_roc_curve(estimator, title, X_test, y_test, fig_roc, col_roc)

    return estimator

def plot_confusion_matrix(estimator, X, fig, col, title=None):
  y_pred = estimator.predict(X)
  tn, fp, fn, tp = confusion_matrix(y_train, y_pred).ravel()
  x = ['pulsar', 'not_pulsar']
  y = ['not_pulsar', 'pulsar']
  z = [[fn, tn], [tp, fp]]
  z_labels = [['(FN)', '(TN)'], ['(TP)', '(FP)']]
  
  for n, row in enumerate(z):
    for m, val in enumerate(row):
      # initialize the annotations array to avoid plotly display bugs
      if col == 1 and n == 0 and m == 0:
        for i in range(3):
          annotations.append(dict(text=(""), x=x[m], y=y[n], xref=('x'+str(col)), yref=('y'+str(col)), showarrow=False))
      annotations.append(dict(text=("{:d}<br>{}".format(z[n][m],z_labels[n][m])), x=x[m], y=y[n], xref=('x'+str(col)), yref=('y'+str(col)), showarrow=False))

  fig.add_trace(go.Heatmap(z=z, x=x, y=y, colorscale = 'Greys', name=""), 1, col)

  fig.update_layout(annotations = annotations, title = title)

def plot_learning_curve(estimator, X, y, cv, n_jobs=-1, train_sizes=np.linspace(.1, 1.0, 5)):
  train_sizes, train_scores, test_scores = learning_curve(estimator, X, y, cv=cv, n_jobs=n_jobs, train_sizes=train_sizes, scoring="f1")
  train_scores_mean = np.mean(train_scores, axis=1)
  train_scores_std = np.std(train_scores, axis=1)
  test_scores_mean = np.mean(test_scores, axis=1)
  test_scores_std = np.std(test_scores, axis=1)
  
  data.append(dict(type='scatter', x=train_sizes, y=train_scores_mean - train_scores_std, mode='lines', name='', showlegend=False,
                    marker=dict(color='blue', size=11, line=dict(color='rgba(217, 217, 217, 0.14)', width=0.1), opacity=0.4), visible=False))
  data.append(dict(type='scatter', x=train_sizes, y=train_scores_mean + train_scores_std, mode='lines', name='', fill="tonexty", showlegend=False,
                    marker=dict(color='blue', size=11, line=dict(color='rgba(217, 217, 217, 0.14)', width=0.1), opacity=0.4), visible=False))
  data.append(dict(type='scatter', x=train_sizes, y=train_scores_mean,  mode='lines', name='Train score', showlegend=True,
                    marker=dict(color='blue', size=11, line=dict(color='rgba(217, 217, 217, 0.14)', width=0.1), opacity=0.7), visible=False))
  data.append(dict(type='scatter', x=train_sizes, y=test_scores_mean - test_scores_std, mode='lines', name='', showlegend=False,
                    marker=dict(color='green', size=11, line=dict(color='rgba(50, 205, 50, 0.14)', width=0.1), opacity=0.4), visible=False))
  data.append(dict(type='scatter', x=train_sizes, y=test_scores_mean + test_scores_std, mode='lines', name='', fill="tonexty", showlegend=False,
                    marker=dict(color='green', size=11, line=dict(color='rgba(50, 205, 50, 0.14)', width=0.1), opacity=0.4), visible=False))
  data.append(dict(type='scatter', x=train_sizes, y=test_scores_mean,  mode='lines', name='Test score', showlegend=True,
                    marker=dict(color='green', size=11, line=dict(color='rgba(50, 205, 50, 0.14)', width=0.1), opacity=0.7), visible=False))
  
def plot_curve_slider(title):
  fig = go.Figure(data=data)
  for i in range(6):
    fig.data[i].visible = True
  steps = []
  labels = ['X_train', '5D-PCA', '1D-LDA']
  for j in range(3):
    step = dict(method="restyle", args=["visible", [False] * len(fig.data)], label = labels[j])
    for i in range(6):
      step["args"][1][j*6+i] = True
    steps.append(step)

  sliders = [dict(active=3, currentvalue = dict(prefix = "Learning Curve on: "), pad={"t": 50}, steps=steps)]
  fig.update_layout(sliders=sliders, xaxis=dict(title='Number of training samples'), yaxis=dict(title='F1 Score'), title = title + " Learning Curves")
  fig.show()
  

def plot_roc_curve(classifier, legend, X_test, y_test, fig, col=1):
  data = []
  data.append(dict(type='scatter', x=[0, 1], y=[0, 1], showlegend=False, mode='lines', name='', line=dict(color='blue')))
  
  y_test_roc = np.array([([0, 1] if y else [1, 0]) for y in y_test])
  y_score = classifier.predict_proba(X_test)
    
  # Compute ROC curve and ROC area for each class
  fpr = dict()
  tpr = dict()
  roc_auc = dict()
  for i in range(2):
    fpr[i], tpr[i], _ = roc_curve(y_test_roc[:, i], y_score[:, i])
    roc_auc[i] = auc(fpr[i], tpr[i])

  # Compute micro-average ROC curve and ROC area
  fpr["micro"], tpr["micro"], _ = roc_curve(y_test_roc.ravel(), y_score.ravel())
  roc_auc["micro"] = auc(fpr["micro"], tpr["micro"])

  data.append(dict(type='scatter', x=fpr['micro'], y=tpr['micro'], showlegend=True, mode='lines', name=legend + " (area = %0.2f)" % roc_auc['micro'],
                hoverlabel = dict(namelength=30)))
      
  fig.update_xaxes(title_text="False Positive Rate", row=1, col=col)
  fig.update_yaxes(title_text="True Positive Rate", row=1, col=col)
  
  for d in data:
    fig.add_trace(d, row=1, col=col)

def plot_var_importance(estimator, df):
  importances = estimator.feature_importances_
  indices = np.argsort(importances)[::-1]
  features = (df.drop('TARGET', axis=1).columns)[indices]
  data = [{"type": "bar", "x": features, "y": importances[indices]}]
  layout = dict(title = "Random Forests Variable Importance", yaxis=dict(title="Variable Importance (%)"))

  fig = go.Figure(data=data, layout=layout)
  fig.show()

def print_scores(classifiers, test_sets, y_test, fig):
  results_df = pd.DataFrame(columns=["accuracy", "precision", "recall", "f1"])
  methods = ["X_train", "5D PCA", "LDA"]
  
  for classifier, X_test, method in zip(classifiers, test_sets, methods):
    y_pred = classifier.predict(X_test)
    entries = []
    entries.append(accuracy_score(y_test, y_pred))
    entries.append(precision_score(y_test, y_pred))
    entries.append(recall_score(y_test, y_pred))
    entries.append(f1_score(y_test, y_pred))
    row = ["%.3f" % r for r in entries]
    results_df.loc[method] = row
  
  df = pd.DataFrame(columns=["", "accuracy", "precision", "recall", "f1"])
  fig.add_trace(go.Table(header=dict(values=list(df.columns), fill = dict(color='#C2D4FF'), align = ['center'] * 5, font = dict(color = '#506784', size = 14), height = 50),
                cells=dict(values=[methods, results_df.accuracy, results_df.precision, results_df.recall, results_df.f1], fill = dict(color='#F5F8FF'), align = ['center'] * 5, 
                           font = dict(color = '#506784', size = 13), height = 40)), row=1, col=2)

def print_scores_lda(classifier, X_test, y_test, fig, col):
  results_df = pd.DataFrame(columns=["accuracy", "precision", "recall", "f1"])
  method = "LDA"
  y_pred = classifier.predict(X_test)
  entries = []
  entries.append(accuracy_score(y_test, y_pred))
  entries.append(precision_score(y_test, y_pred))
  entries.append(recall_score(y_test, y_pred))
  entries.append(f1_score(y_test, y_pred))
  row = ["%.3f" % r for r in entries]
  results_df.loc[method] = row

  df = pd.DataFrame(columns=["", "accuracy", "precision", "recall", "f1"])
  
  fig.add_trace(go.Table(header=dict(values=list(df.columns), fill = dict(color='#C2D4FF'), align = ['center'] * 5, font = dict(color = '#506784', size = 14), height = 50),
                cells=dict(values=[[method], results_df.accuracy, results_df.precision, results_df.recall, results_df.f1], fill = dict(color='#F5F8FF'), align = ['center'] * 5, 
                           font = dict(color = '#506784', size = 13), height = 40)), row=1, col=col)


def plot_roc_curve_comparison(classifiers, legends, X_test, y_test, fig, col=1):
  data = []
  data.append(dict(type='scatter', x=[0, 1], y=[0, 1], showlegend=False, mode='lines', name='', line=dict(color='blue')))
  
  for classifier, legend in zip(classifiers, legends):
    y_test_roc = np.array([([0, 1] if y else [1, 0]) for y in y_test])
    y_score = classifier.predict_proba(X_test)
      
    # Compute ROC curve and ROC area for each class
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(2):
      fpr[i], tpr[i], _ = roc_curve(y_test_roc[:, i], y_score[:, i])
      roc_auc[i] = auc(fpr[i], tpr[i])

    # Compute micro-average ROC curve and ROC area
    fpr["micro"], tpr["micro"], _ = roc_curve(y_test_roc.ravel(), y_score.ravel())
    roc_auc["micro"] = auc(fpr["micro"], tpr["micro"])

    data.append(dict(type='scatter', x=fpr['micro'], y=tpr['micro'], showlegend=True, mode='lines', name=legend + " (area = %0.2f)" % roc_auc['micro'],
                  hoverlabel = dict(namelength=30)))
        
  fig.update_xaxes(title_text="False Positive Rate", row=1, col=col)
  fig.update_yaxes(title_text="True Positive Rate", row=1, col=col)
  
  for d in data:
    fig.add_trace(d, row=1, col=col)

def print_scores_comparisons(classifiers, X_test, y_test, fig, methods):
  results_df = pd.DataFrame(columns=["accuracy", "precision", "recall", "f1"])
  best_value = 0

  for classifier, method in zip(classifiers, methods):
    y_pred = classifier.predict(X_test)
    entries = []
    entries.append(accuracy_score(y_test, y_pred))
    entries.append(precision_score(y_test, y_pred))
    entries.append(recall_score(y_test, y_pred))
    entries.append(f1_score(y_test, y_pred))
    row = ["%.3f" % r for r in entries]
    results_df.loc[method] = row
    if np.mean(entries) > best_value:
      best_value = np.mean(entries)
      best_classifier = method

  df = pd.DataFrame(columns=["", "accuracy", "precision", "recall", "f1"])
  fig.add_trace(go.Table(header=dict(values=list(df.columns), fill = dict(color='#C2D4FF'), align = ['center'] * 5, font = dict(color = '#506784', size = 14), height = 50),
                cells=dict(values=[methods, results_df.accuracy, results_df.precision, results_df.recall, results_df.f1], fill = dict(color='#F5F8FF'), align = ['center'] * 5, 
                           font = dict(color = '#506784', size = 13), height = 40)), row=1, col=2)
  return best_classifier

pca = PCA(n_components=5, random_state=1)
pca_5D = pca.fit_transform(X_train)
test_5D = pca.transform(X_test)
test_lda = lda.transform(X_test)
test_sets = [X_test, test_5D, test_lda]
best_classifiers = []
method_legend = []

**LDA for Classification**

Linear Discriminant Analisys can also be used for classification.<br>
The algorithm tries to estimate a probability of the sample to belong to a given class:
\begin{equation*}
P(C = c_i|X = x) = \frac{P(X = x|C = c_i)P(C = c_i)}{\sum_{j=1}^{2}P(X = x|C = c_j)P(C = c_j)}
\end{equation*}
where $C = \{c_1, c_2\}$ are the two classes: pulsar and not pulsar, $X$ is the domain and $x$ is the specific sample.<br>
The assumption behind the algorithm is that each class can be modeled as a multivariate Gaussian distribution and share the covariance matrix $\sum$. 
\begin{equation*}
P(X = x|C = c_i) = \frac{1}{\sqrt{2\pi}|\sum|^\frac{1}{2}}e^{-\frac{1}{2}(x-\mu c_i)^T\sum^{-1}(x-\mu c_i)}
\end{equation*}
where $\mu c_i$ is the mean vector for class $c_i$.<br>
The LDA fitting produces *m* discriminant function. In our case *m* is equal 2 (number of classes). These function are used to classify each sample and then the decision boundary used are the ones where the discriminant functions equal each other.<br>
Also the class centroids $\mu c_i$ can be used to classify samples.


In [16]:
#@title
method = "LDA"
annotations = []
data = []

col_conf = 1
col_roc = 2
col_scores = 3
 
# lda on X_train
plot_title = "X_train"
fig_matrix = make_subplots(rows=1, cols=3, specs=[[{"type": "heatmap"}, {"type": "xy"}, {"type": "table"}]], subplot_titles=("Confusion Matrix", method + " ROC Curve", "Test Scores"))

clf = grid_search_matrix(lda, X_train, y_train, X_test, y_test, None, plot_title, None, fig_matrix, fig_matrix, col_conf, col_roc=col_roc)
fig = go.Figure(data=data)
for i in range(6):
  fig.data[i].visible = True
fig.update_layout(xaxis=dict(title='Number of training samples'), yaxis=dict(title='F1 Score'), title = "Learning Curve")
fig.show()
print_scores_lda(clf, X_test, y_test, fig_matrix, col_scores)
fig_matrix.update_layout(dict(legend=dict(x = 1, y=-0.2, orientation="h")))
fig_matrix.show()

best_classifiers.append(clf)
method_legend.append(method)

**Logistic Regression**

Logistic regression is a regression method useful to classify binary variables. Our dataset is compatible with this kind of analisys as we have to choose between *pulsas* or *not pulsar* samples.<br>

The formula can be easily derived starting from the *linear regression* one:
\begin{equation*}
y  = \beta_0+\beta_1x
\end{equation*}
The above formula states a linear model, the *logistic regression* is instead based on a sigmoid funcion:<br>
\begin{equation*}
\Phi_x  = \frac{1}{1+e^{-x}}
\end{equation*}

That applied to the linear regression formula above gives:
\begin{equation*}
p  = \frac{1}{1+e^{-(\beta_0+\beta_1x)}}
\end{equation*}
where *p* is bounded from 0 to 1 and represent the probability.<br>
The formula above can be then extended to *n* variables:
\begin{equation*}
p  = \frac{1}{1+e^{-(\beta_0+\beta_1x_1+\beta_2x_2+...+\beta_nx_n)}}
\end{equation*}
The model used is from the sklearn library and the hyperparameters to drive the grid search are:
* solver : [liblinear] preferred choice for relative small datasets such ours
* penalty: [l1, l2] norm used for penalization
* C: [np.linspace(0.1, 10, 10)] regularization factor

In [17]:
#@title
logistic_regression_parameters = {
    'solver' : ['liblinear'],     # since this is a small dataset, this is the preferred choice
    'penalty' : ['l1', 'l2'],
    'max_iter' : [1000],
    'C' : np.linspace(0.1, 10, 10),
    'random_state': [1]
  }

method = "Logistic Regression"
annotations = []
data = []
classifiers = []
lr = LogisticRegression()
fig_matrix = make_subplots(rows=1, cols=3, subplot_titles=("Original", "PCA", "LDA"))
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=(method + " ROC Curve", "Test Scores"))

# logistic regression on X_train
plot_title = "X_train"
clf = grid_search_matrix(lr, X_train, y_train, X_test, y_test, 5, plot_title, logistic_regression_parameters, fig_matrix, fig_roc, 1)
classifiers.append(clf)

# logistic regression on 5_pca_components
plot_title = "5D PCA"
clf = grid_search_matrix(lr, pca_5D, y_train, test_5D, y_test, 5, plot_title, logistic_regression_parameters, fig_matrix, fig_roc, 2)
classifiers.append(clf)

# logistic regression on LDA
plot_title = "LDA"
clf = grid_search_matrix(lr, lda_1D, y_train, test_lda, y_test, 5, plot_title, logistic_regression_parameters, fig_matrix, fig_roc, 3)
classifiers.append(clf)

plot_curve_slider(method)
fig_matrix.show()
print_scores(classifiers, test_sets, y_test, fig_roc)
fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
fig_roc.show()

best_classifiers.append(classifiers[0])
method_legend.append(method)

**Decision Trees**

A *decision tree* is a tree where each node represents a feature, each link a decision and each leaf a value.
The tree is built using a recursive greedy algorithm that identifies ways to split data based on a set of conditions.<br>
Trying to find the best accurate and the smallest possible decision tree is an NP-hard problem 
The major criticality of the algorithm is the method adopted to perform the split. It can be based on the *gini index* or on the *entropy* measure. The first one calculate if the elements considered ar part of the same population.
The *Gini* split formula is the one below:
\begin{equation*}
Gini = 1-\sum_{i=1}^{C}p_i^2
\end{equation*}
The other way is based on information gain and entropy that is a measure of impurity, how uncertain something is:
\begin{equation*}
Entropy = \sum_{i=1}^{C}-p_i*log_2(p_i)
\end{equation*}
where $C$ is the number of classes.<br>

The model used is from the sklearn library and the hyperparameters to drive the grid search are:
* criterion : [gini, entropy] function to measure the quality of the split
* max_depth: [np.linspace(2, 100, 5)] max possible depth used to have leaves

In [19]:
#@title
decision_tree_parameters = {
    'criterion': ['gini', 'entropy'],
    'max_depth': np.linspace(2, 100, 5, dtype='int'),
    'random_state': [1]
}

method = "Decision Trees"
annotations = []
data = []
classifiers = []
dt = DecisionTreeClassifier()
fig_matrix = make_subplots(rows=1, cols=3, subplot_titles=("Original","PCA", "LDA"))
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=(method + " ROC Curve", "Test Scores"))

# decision tree on X_train
plot_title = "X_train"
clf = grid_search_matrix(dt, X_train, y_train, X_test, y_test, 5, plot_title, decision_tree_parameters, fig_matrix, fig_roc, 1)
classifiers.append(clf)

# decision tree on 5_pca_components
plot_title = "5D PCA"
clf = grid_search_matrix(dt, pca_5D, y_train, test_5D, y_test, 5, plot_title, decision_tree_parameters, fig_matrix, fig_roc, 2)
classifiers.append(clf)

# decision tree on LDA
plot_title = "LDA"
clf = grid_search_matrix(dt, lda_1D, y_train, test_lda, y_test, 5, plot_title, decision_tree_parameters, fig_matrix, fig_roc, 3)
classifiers.append(clf)

plot_curve_slider(method)
fig_matrix.show()
print_scores(classifiers, test_sets, y_test, fig_roc)
fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
fig_roc.show()

best_classifiers.append(classifiers[0])
method_legend.append(method)

**KNN**

The K-Nearest Neighbors algorithm is a non-parametric method that compute the idea of similarity using the distance between points.
The k states how many element will be used to discriminate the class of the given sample, as a majority vote of its neighbors.
This algorithm calculates the distance of a single sample from every other samples of the dataset. Speaking of distances, the most common is the Euclidean.

The model used is from the sklearn library and the hyperparameters to drive the grid search are:

* n_neighbors : [1, 2, 3, 5] number of neighbors
* weights: [uniform, distance] weight function used in prediction
* p: [1, 2] power parameter for the Minkowski metric, p = 1 Manhattan and p = 2 Euclidian

Let's see the Minkowski formula:
\begin{equation*}
Minkowski = ({\sum_{i=1}^{k}(|x_i-y_i|)^p})^\frac{1}{p}
\end{equation*}

In [20]:
knn_parameters = {
    'n_jobs' : [1],
    'n_neighbors': [1, 2, 3, 5],
    'weights': ['uniform', 'distance'],
    'p': [1, 2], # 1 = Manhattan, 2 = Euclidean
}

method = "KNN"
annotations = []
data = []
classifiers = []
knn = KNeighborsClassifier()
fig_matrix = make_subplots(rows=1, cols=3, subplot_titles=("Original","PCA", "LDA"))
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=(method + " ROC Curve", "Test Scores"))

# decision tree on X_train
plot_title = "X_train"
clf = grid_search_matrix(knn, X_train, y_train, X_test, y_test, 5, plot_title, knn_parameters, fig_matrix, fig_roc, 1)
classifiers.append(clf)

# decision tree on 5_pca_components
plot_title = "5D PCA"
clf = grid_search_matrix(knn, pca_5D, y_train, test_5D, y_test, 5, plot_title, knn_parameters, fig_matrix, fig_roc, 2)
classifiers.append(clf)

# decision tree on LDA
plot_title = "LDA"
clf = grid_search_matrix(knn, lda_1D, y_train, test_lda, y_test, 5, plot_title, knn_parameters, fig_matrix, fig_roc, 3)
classifiers.append(clf)

plot_curve_slider(method)
fig_matrix.show()
print_scores(classifiers, test_sets, y_test, fig_roc)
fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
fig_roc.show()

best_classifiers.append(classifiers[0])
method_legend.append(method)

**Random Forests**

In [0]:
#@title
random_forests_parameters = {
    'n_jobs' : [1],
    'n_estimators' : [50, 75, 100],
    'random_state': [1]
}

method = "Random Forests"
annotations = []
data = []
classifiers = []
rf = RandomForestClassifier()
fig_matrix = make_subplots(rows=1, cols=3, subplot_titles=("Original", "PCA", "LDA"))
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=(method + " ROC Curve", "Test Scores"))

# random forests on X_train
plot_title = "X_train"
clf = grid_search_matrix(rf, X_train, y_train, X_test, y_test, 5, plot_title, random_forests_parameters, fig_matrix, fig_roc, 1, var_importance=True)
classifiers.append(clf)

# random forests on 5_pca_components
plot_title = "5D PCA"
clf = grid_search_matrix(rf, pca_5D, y_train, test_5D, y_test, 5, plot_title, random_forests_parameters, fig_matrix, fig_roc, 2)
classifiers.append(clf)

# random forests on LDA
plot_title = "LDA"
clf = grid_search_matrix(rf, lda_1D, y_train, test_lda, y_test, 5, plot_title, random_forests_parameters, fig_matrix, fig_roc, 3)
classifiers.append(clf)

plot_curve_slider(method)
fig_matrix.show()
print_scores(classifiers, test_sets, y_test, fig_roc)
fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
fig_roc.show()

best_classifiers.append(classifiers[0])
method_legend.append(method)

**Linear SVM**

In [0]:
#@title
svm_parameters = {
  'kernel': ['linear'],
  'C': np.linspace(1, 100, 3, dtype='int'),
  'random_state': [1],
  'probability' : [True]
}

method = "Linear SVM"
annotations = []
data = []
classifiers = []
svm = SVC()
fig_matrix = make_subplots(rows=1, cols=3, subplot_titles=("Original", "PCA", "LDA"))
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=(method + " ROC Curve", "Test Scores"))

with warnings.catch_warnings():
  warnings.simplefilter("ignore")
  # SVM on X_train
  plot_title = "X_train"
  clf = grid_search_matrix(svm, X_train, y_train, X_test, y_test, 5, plot_title, svm_parameters, fig_matrix, fig_roc, 1)
  classifiers.append(clf)

  # SVM on 5_pca_components
  plot_title = "5D PCA"
  clf = grid_search_matrix(svm, pca_5D, y_train, test_5D, y_test, 5, plot_title, svm_parameters, fig_matrix, fig_roc, 2)
  classifiers.append(clf)

  # SVM on LDA
  plot_title = "LDA"
  clf = grid_search_matrix(svm, lda_1D, y_train, test_lda, y_test, 5, plot_title, svm_parameters, fig_matrix, fig_roc, 3)
  classifiers.append(clf)

  plot_curve_slider(method)
  fig_matrix.show()
  print_scores(classifiers, test_sets, y_test, fig_roc)
  fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
  fig_roc.show()

  best_classifiers.append(classifiers[0])
  method_legend.append(method)

**Gaussian Kernel SVM**

In [0]:
#@title
svm_parameters = {
  'kernel': ['rbf'],
  'C': np.linspace(0.001, 10, 4),
  'gamma': np.linspace(0.001, 10, 4),
  'random_state': [1],
  'probability' : [True]
}

method = "Gaussian Kernel SVM"
annotations = []
data = []
classifiers = []
svm = SVC()
fig_matrix = make_subplots(rows=1, cols=3, subplot_titles=("Original", "PCA", "LDA"))
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=(method + " ROC Curve", "Test Scores"))

with warnings.catch_warnings():
  warnings.simplefilter("ignore")
  # SVM on X_train
  plot_title = "X_train"
  clf = grid_search_matrix(svm, X_train, y_train, X_test, y_test, 5, plot_title, svm_parameters, fig_matrix, fig_roc, 1, n_jobs=-1)
  classifiers.append(clf)

  # SVM on 5_pca_components
  plot_title = "5D PCA"
  clf = grid_search_matrix(svm, pca_5D, y_train, test_5D, y_test, 5, plot_title, svm_parameters, fig_matrix, fig_roc, 2, n_jobs=-1)
  classifiers.append(clf)

  # SVM on LDA
  plot_title = "LDA"
  clf = grid_search_matrix(svm, lda_1D, y_train, test_lda, y_test, 5, plot_title, svm_parameters, fig_matrix, fig_roc, 3, n_jobs=-1)
  classifiers.append(clf)

  plot_curve_slider(method)
  fig_matrix.show()
  print_scores(classifiers, test_sets, y_test, fig_roc)
  fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
  fig_roc.show()

  best_classifiers.append(classifiers[0])
  method_legend.append(method)

**Comparisons**

After every single algorithm, we do a comparison of all.<br>
As can be see from the ROC curve the algorithms are all almost comparable with little differences.<br>
The best performing classifier is the Random Forest that is in fact the best according to this formula:
\begin{equation*}
average  = \frac{accuracy + precision + recall + f1}{4}
\end{equation*}


In [0]:
#@title
fig_roc = make_subplots(rows=1, cols=2, specs=[[{"type": "xy"}, {"type": "table"}]], subplot_titles=("ROC Curve Comparisons", "Test Scores"))
plot_roc_curve_comparison(best_classifiers, method_legend, X_test, y_test, fig_roc)
best_one = print_scores_comparisons(best_classifiers, X_test, y_test, fig_roc, method_legend)
fig_roc.update_layout(dict(legend=dict(y=-0.2, orientation="h")))
fig_roc.show()

print('The best classifier is the ' + best_one)

The best classifier is the Random Forests
